In [1]:
import pandas as pd
import requests
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
import time
import numpy as np
from urllib.parse import urljoin
import xlsxwriter
from openpyxl import load_workbook
import re

In [2]:
def append_df_to_excel(filename, df, sheet_name='Sheet1', startrow=None,
                       truncate_sheet=False, 
                       **to_excel_kwargs):
    """
    Append a DataFrame [df] to existing Excel file [filename]
    into [sheet_name] Sheet.
    If [filename] doesn't exist, then this function will create it.

    Parameters:
      filename : File path or existing ExcelWriter
                 (Example: '/path/to/file.xlsx')
      df : dataframe to save to workbook
      sheet_name : Name of sheet which will contain DataFrame.
                   (default: 'Sheet1')
      startrow : upper left cell row to dump data frame.
                 Per default (startrow=None) calculate the last row
                 in the existing DF and write to the next row...
      truncate_sheet : truncate (remove and recreate) [sheet_name]
                       before writing DataFrame to Excel file
      to_excel_kwargs : arguments which will be passed to `DataFrame.to_excel()`
                        [can be dictionary]

    Returns: None
    """
    from openpyxl import load_workbook
    
    # ignore [engine] parameter if it was passed
    if 'engine' in to_excel_kwargs:
        to_excel_kwargs.pop('engine')

    writer = pd.ExcelWriter(filename, engine='openpyxl')

    try:
        # try to open an existing workbook
        writer.book = load_workbook(filename)

        # get the last row in the existing Excel sheet
        # if it was not specified explicitly
        if startrow is None and sheet_name in writer.book.sheetnames:
            startrow = writer.book[sheet_name].max_row

        # truncate sheet
        if truncate_sheet and sheet_name in writer.book.sheetnames:
            # index of [sheet_name] sheet
            idx = writer.book.sheetnames.index(sheet_name)
            # remove [sheet_name]
            writer.book.remove(writer.book.worksheets[idx])
            # create an empty sheet [sheet_name] using old index
            writer.book.create_sheet(sheet_name, idx)

        # copy existing sheets
        writer.sheets = {ws.title:ws for ws in writer.book.worksheets}
    except FileNotFoundError:
        # file does not exist yet, we will create it
        pass

    if startrow is None:
        startrow = 0

    # write out the new sheet
    df.to_excel(writer, sheet_name, startrow=startrow, **to_excel_kwargs)
    
    # save the workbook
    writer.save()

In [3]:
# load overview over municipalities
df = pd.read_excel("../data/NRW/nrw_mun.xlsx")

# select rows and columns
muns = df.loc[df['Wer']=='Edith', ['Gemeinde', 'Gemeindeschlüssel']]
muns.columns = ['mun_name', 'mun_code']

In [4]:
def get_url1(name):
    e.send_keys(name)
    e.send_keys(Keys.ENTER)
    soup = BeautifulSoup(d.page_source)
    d.find_element_by_id('suchfeld').clear()
    time.sleep(0.7)
    links = soup.find('tbody').find_all('a') 
    return [link.get('href') for link in links if 'Votemanager' not in link]

In [5]:
# set up webdriver and search field element
# d=webdriver.Chrome("../chromedriver.exe")
# d.get('https://wahlen.votemanager.de/#')
# e = d.find_element_by_id('suchfeld')

# # search for each municipality and get the url to the municipality specific overview page
# muns['url'] = muns['mun_name'].apply(get_url1)

In [6]:
# muns.to_pickle("./temp.pkl")
muns = pd.read_pickle("./temp.pkl")

In [7]:
muns.head()

mun_name  mun_code  \
1              Duisburg   5112000   
5   Mülheim an der Ruhr   5117000   
9             Wuppertal   5124000   
13                 Goch   5154016   
17             Kevelaer   5154032   

                                                  url  
1   [http://wahlergebnis.duisburg.de/05112000/inde...  
5   [https://wahlpraesentation.muelheim-ruhr.de/05...  
9   [https://wahlen.wuppertal.de/05124000/index.html]  
13                                                 []  
17                                                 []

In [8]:
# clean results:

# 1. export municipalities that weren't found on votemanager
writer = pd.ExcelWriter('../data/NRW/nrw_mun_edith.xlsx', engine='xlsxwriter')

muns[muns.astype(str)['url']=='[]'][['mun_name', 'mun_code']].to_excel(writer, 'by hand', index=False)

muns = muns[muns.astype(str)['url']!='[]'].reset_index(drop=True)

writer.save()

# 2. look at municipalities were 2 results were found
muns['results'] = muns['url'].str.len()

muns['url1'] = np.nan

for row in muns.itertuples():
    if row[4] == 1:
        muns.loc[row[0], 'url1'] = row[3]
    if row[4] > 1:
        muns.loc[row[0], 'url1'] = [link for link in row[3] if str(row[2]) in link]
        
muns.drop(columns=['url', 'results'], inplace=True)

In [9]:
# now, direct to the elections on 25-05-2014
def get_url2(url1):
    """ To get the urls specific to the Ratswahl elections.
    It takes as input the overview url for each municipality from wahlen.regioit
    and returns a list of all Ratswahl-url from its html text.
    """
    base = url1
    r = requests.get(url1)
    soup = BeautifulSoup(r.text)
    
    kom_row  = [ r for r in soup.find_all('tr') if 'Kommunalwahlen' in r.text ]
    
    res = [link.get('href') for link in BeautifulSoup(str(kom_row)).find_all('a') if '25.05.2014' in link]
    
    if res:
        href=res.pop()
        return urljoin(base,href)
    else:
        return np.nan

In [10]:
muns['url2'] = muns['url1'].apply(get_url2)

In [11]:
# remember to safe those with to excel writer!!!
reader = pd.read_excel('../data/NRW/nrw_mun_edith.xlsx')

append_df_to_excel('../data/NRW/nrw_mun_edith.xlsx', muns[muns['url2'].isnull()][['mun_name', 'mun_code']],
                   sheet_name="by hand", startcol=0, startrow=len(reader)+1)

muns.dropna(axis=0, inplace=True)

In [12]:
# From the overview url set up url for the overview of Wahlbezirke for Ratswahl:
# muns['url3'] = 

def get_url3(url2): 
    r = requests.get(url2) 
    soup = BeautifulSoup(r.text)
    base = url2
    hrefs = [link.get('href') for link in soup.find_all('a')]
    
    matches = ['Ratswahl', 'Landratswahl']
    
    res=[href for href in hrefs if any(x in href for x in matches)]
    
    if res:
        s = res.pop()
        href = re.sub('Gemeinde_.*','Uebersicht_wahlb.html', s)
        return urljoin(base,href)
    else:
        return np.nan

In [13]:
muns['url3'] = muns['url2'].apply(get_url3)

In [14]:
# remember to safe those with to excel writer!!!

reader = pd.read_excel('../data/NRW/nrw_mun_edith.xlsx')

append_df_to_excel('../data/NRW/nrw_mun_edith.xlsx', muns[muns['url3'].isnull()][['mun_name', 'mun_code']],
                   sheet_name="by hand", startcol=0, startrow=len(reader)+1)

muns.dropna(axis=0, inplace=True)

In [15]:
muns.reset_index(drop=True, inplace=True)

In [16]:
def p2f(x):
    return float(x.strip(' %').replace(',','.'))/100


cols = ['votes', 'share', 'candidate', 'party', 'district', 'number', 'mun', 'mun_code']
df_final = pd.DataFrame(columns=cols)

In [17]:
# get all the Wahlbezirke
for i in range(1,len(muns.index.values)):
    display(i, muns.loc[i,'mun_name'])
    
    base = muns.loc[i, 'url2']
    url3 = muns.loc[i, 'url3']

    href_bezirke = [row.get('href') for row in BeautifulSoup(requests.get(url3).text).find('table').find_all('a')[:-1]]
    
    url_bezirke = [urljoin(base,href) for href in href_bezirke]
    
    for x in range(len(url_bezirke)): 
        url = url_bezirke[x]
        soup = BeautifulSoup(requests.get(url).text)
        
        tables = soup.find_all('table')
        
        if tables != []:
            results = pd.read_html(str(tables[1]))[0].iloc[:, 1:]
            results[['candidate','party']]  = results.iloc[:,0].str.split(',', expand=True, n=1)
            results.drop(results.columns[0], axis=1, inplace=True)
            results.iloc[:,1]=results.iloc[:,1].apply(p2f)
        
        else:
            results=pd.DataFrame(index=[0], columns=cols)
        
        re_searchnum = re.search('[0-9]+_(.*)\.html',href_bezirke[x])
                                 
        if (re_searchnum is not None):
            results['district'] = str(re_searchnum.group(1)).replace('__',' ')
            results['number'] = int(re.findall('[0-9]+',href_bezirke[x]).pop())
        else:
            results['district'] = str(re.search('Wahlbezirk_(.*)\.html', href_bezirke[x]).group(1))
            results['number'] = x+1

        results['mun'] = muns.loc[i,'mun_name']
        results['mun_code'] = muns.loc[i,'mun_code']
        results.columns = cols   
        
        df_final = df_final.append(results)
    
    

1

'Mülheim an der Ruhr'

2

'Wuppertal'

3

...

'Wickede (Ruhr)'

68

'Holzwickede'

69

'Selm'

In [18]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):  
    display(df_final)

votes   share                                     candidate  \
0     538  0.2863                                        Körner   
1     419   0.223                                    Oesterwind   
2     209  0.1112                                von Wedelstädt   
3     163  0.0867                                        Mangen   
4     218   0.116                                       Niehoff   
5      87  0.0463                                         Wolff   
6      29  0.0154                                        Schlos   
7      16  0.0085                                   Schmidtchen   
8      13  0.0069                                     Dr. Grein   
9     117  0.0623                                       Viljoen   
10     46  0.0245                                         Tasch   
11     24  0.0128                                       Raphael   
0     491  0.3711                                         Bakum   
1     246  0.1859                                       Küsters   
2      84  0.0635                                      Luthmann   
3      41   0.031                                     Pollmeier   
4     139  0.1051                                          Loef   
5     104  0.0786                                       Thunack   
6      35  0.0265                                        Handke   
7      29  0.0219                                   Matuszewski   
8      11  0.0083                                      Babanawo   
9      68  0.0514                                         Fritz   
10     31  0.0234                                      Bartmann   
11     44  0.0333                                     Grohsmann   
0     732  0.3624                                      Scholten   
1     414   0.205                                    Kampermann   
2     211  0.1045                                        Scholl   
3      70  0.0347                                        Schulz   
4     225  0.1114                                           Erd   
5     110  0.0545                                    Felderhoff   
6      35  0.0173                                       Dalheim   
7      15  0.0074                                     Osterhage   
8      23  0.0114                                         Turan   
9     105   0.052                                         Fritz   
10     36  0.0178                                        Qengaj   
11     44  0.0218                                         Butta   
0     774  0.3315                                          Böhm   
1     447  0.1914                                         Medic   
2     255  0.1092                                    Sporkhorst   
3     140    0.06                                        Mangen   
4     245  0.1049                                     de Bruijn   
5     149  0.0638                                          Hong   
6      46  0.0197                                       Klabuhn   
7      15  0.0064                                       Vitasek   
8      19  0.0081                                      Feldmann   
9     146  0.0625                                         Immel   
10     48  0.0206                                        Keppel   
11     51  0.0218                                        Müller   
0     830  0.2432                                          Marx   
1   1.011  0.2962                                          Püll   
2     380  0.1113                                    Sporkhorst   
3     296  0.0867                                        Kubiak   
4     503  0.1474                                         Weber   
5      98  0.0287                                        Gerbig   
6      25  0.0073                                       Klabuhn   
7      19  0.0056                                     Schreiber   
8      21  0.0062                                        Krstin   
9     124  0.0363                                        Wessel   
10     49  0.0144                                  

In [19]:
append_df_to_excel('../data/NRW/nrw_mun_edith.xlsx', df_final,
                   sheet_name="scraped", startcol=0, startrow=0)